# Imports

In [23]:
from IPython.lib.deepreload import reload

%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [24]:
from llm_calc.lib.experiment import  ls_client, make_df
from llm_calc.lib.config import config
from llm_calc.lib.datamodel import Arm, ArmSlug, Model, ModelSlug
from llm_calc.lib.datacore import datacore
from os.path import join as path_join
import plotly.graph_objects as go
import plotly.express as px
import pandas as pd
arms = datacore.arms
models = datacore.models
calculators = datacore.calculators
import numpy as np
from llm_calc.util import util
from os import error
import plotly.express as px

In [25]:
# import data
df = pd.read_pickle(path_join(config.RESULTS_DATA_PATH,"most_recent/dataset_results_most-recent.pkl"))

# Data cleaning

In [26]:

# Create a new column for the calculator-arm permutations
df['calculator_arm'] = df.apply(lambda x: f"{x['calculator_slug']} - {x['arm_slug']}", axis=1)

# Make adjusted clincal errors out of 100 instead of 1
df.adjusted_clinical_error_absolute = df.adjusted_clinical_error_absolute * 100
df.adjusted_clinical_error_real = df.adjusted_clinical_error_real * 100
# same for second method
df['adjusted_clinical_error_2_absolute'] = df.adjusted_clinical_error_2_absolute * 100
df['adjusted_clinical_error_2_real'] = df.adjusted_clinical_error_2_real * 100
# and for percentage error
df.percentage_error_real = df.percentage_error_real * 100
df.percentage_error_absolute = df.percentage_error_absolute * 100

# make log versions of the errors
df['adjusted_clinical_error_absolute_log'] = np.log10(df.adjusted_clinical_error_absolute)
df['adjusted_clinical_error_real_log'] = np.log10(df.adjusted_clinical_error_real)
df['adjusted_clinical_error_2_absolute_log'] = np.log10(df.adjusted_clinical_error_2_absolute)
df['adjusted_clinical_error_2_real_log'] = np.log10(df.adjusted_clinical_error_2_real)
df['percentage_error_real_log'] = np.log10(df.percentage_error_real)
df['percentage_error_absolute_log'] = np.log10(df.percentage_error_absolute)


# set the minimum of the log errors to -1
# df['adjusted_clinical_error_absolute_log'] = df['adjusted_clinical_error_absolute_log'].apply(lambda x: -1 if x < -1 else x)
# df['adjusted_clinical_error_real_log'] = df['adjusted_clinical_error_real_log'].apply(lambda x: -1 if x < -1 else x)

/Users/alexandergoodell/.virtualenvs/llm-calc/lib/python3.11/site-packages/pandas/core/arraylike.py:399: RuntimeWarning:

divide by zero encountered in log10

/Users/alexandergoodell/.virtualenvs/llm-calc/lib/python3.11/site-packages/pandas/core/arraylike.py:399: RuntimeWarning:

divide by zero encountered in log10

/Users/alexandergoodell/.virtualenvs/llm-calc/lib/python3.11/site-packages/pandas/core/arraylike.py:399: RuntimeWarning:

invalid value encountered in log10

/Users/alexandergoodell/.virtualenvs/llm-calc/lib/python3.11/site-packages/pandas/core/arraylike.py:399: RuntimeWarning:

divide by zero encountered in log10

/Users/alexandergoodell/.virtualenvs/llm-calc/lib/python3.11/site-packages/pandas/core/arraylike.py:399: RuntimeWarning:

divide by zero encountered in log10

/Users/alexandergoodell/.virtualenvs/llm-calc/lib/python3.11/site-packages/pandas/core/arraylike.py:399: RuntimeWarning:

invalid value encountered in log10

/Users/alexandergoodell/.virtualenvs/llm-calc/li

In [27]:

calculators = datacore.calculators # type: ignore
calculator_cutoffs = {calc.slug.value: (calc.mild_cutoff, calc.severe_cutoff) for calc in calculators} # type: ignore
calculator_min_max = {calc.slug.value: (calc.minimum_score, calc.maximum_score) for calc in calculators} # type: ignore


In [28]:
df['mild_cutoff'] = df.calculator_slug.apply(lambda x: calculator_cutoffs[x][0])
df['severe_cutoff'] = df.calculator_slug.apply(lambda x: calculator_cutoffs[x][1])

df['minimum_score'] = df.calculator_slug.apply(lambda x: calculator_min_max[x][0])
df['maximum_score'] = df.calculator_slug.apply(lambda x: calculator_min_max[x][1])

In [29]:
# Sort the dataframe by adjusted_clinical_error_real
from numpy import sort
df_trimmed = df
sorting_df_real = df_trimmed.groupby(['calculator_arm']).adjusted_clinical_error_real.mean().sort_values(ascending=False).reset_index()
sorting_df_absolute = df_trimmed.groupby(['calculator_arm']).adjusted_clinical_error_absolute.mean().sort_values(ascending=False).reset_index()
sorted_df_real = df_trimmed.set_index('calculator_arm').loc[sorting_df_real.calculator_arm]
sorted_df_absolute = df_trimmed.set_index('calculator_arm').loc[sorting_df_absolute.calculator_arm]



is_excluded_real = (sorting_df_real.adjusted_clinical_error_real == 0)
excluded_real = sorting_df_real[is_excluded_real].calculator_arm.unique()

is_excluded_absolute = (sorting_df_absolute.adjusted_clinical_error_absolute == 0)
excluded_absolute = sorting_df_absolute[is_excluded_absolute].calculator_arm.unique()



In [30]:
sorted_df_real.loc[excluded_real, 'group_real'] = 'excluded'
sorted_df_absolute.loc[excluded_absolute, 'group_absolute'] = 'excluded'

In [31]:
sorted_df_real.reset_index(inplace=True)
sorted_df_absolute.reset_index(inplace=True)

sorted_df_real.loc[sorted_df_real['group_real'] == 'excluded', "calculator_arm"] = "Multiple*"
sorted_df_absolute.loc[sorted_df_absolute['group_absolute'] == 'excluded', "calculator_arm"] = "Multiple*"

# Real (not absolute) error

In [34]:

excluded_calculator_arms_formatted = "".join([f" {arm},<br> " if i % 2 == 1 else f"{arm}, " for i, arm in enumerate(excluded_real[1:])]) + " and " + excluded_real[-1]
exclusion_note = "Multiple calculator-arms represented by single <br> row due to identical adjusted clinical <br> error of zero. These included: <br> " + excluded_calculator_arms_formatted

# Create the scatter plot
fig = px.strip(sorted_df_real, x='adjusted_clinical_error_real', y='calculator_arm', title='Adjusted Clinical Error Real by Calculator-Arm Permutations')
fig.update_traces(jitter=0.2)

# Update layout for better visualization
fig.update_traces(marker=dict(opacity=0.5))  # Set marker opacity to 0.5 for semi-transparency
fig.update_layout(
    xaxis_title='Numeric error, normalized to calculator range',
    yaxis_title='Calculator-Arm Permutations',
    width=800,
    height=1200,
    font=dict(
        family="Arial",
        size=10,
        color="Black"
    ),
    plot_bgcolor="white",
    margin_t=50,
    margin_b=50,
    margin_l=50,
    margin_r=50,
    xaxis=dict(
        range=[-1000, 1000],
        ),  # Set x-axis range
    annotations=[
        # dict(
        #     x=100,
        #     y='cci - llama_ci',
        #     xref='x',
        #     yref='y',
        #     text='Not shown: Three data points > 100',
        #     showarrow=True,
        #     arrowhead=2,
        #     ax=-120,
        #     ay=-0
        # ),
        dict(
            text=exclusion_note,
            align='left',
            # showarrow=False,
            xref='x',
            yref='y',
            x=0,
            y="Multiple*",
            bordercolor='black',
            borderwidth=1,
            ax=150,
            ay=30
        )
    ]
)

util.save_fig(fig, "adjusted_clinical_error_real_by_calculator_arm")
fig.show()

Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/adjusted_clinical_error_real_by_calculator_arm.svg
Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/adjusted_clinical_error_real_by_calculator_arm.png


# Sorted by performance, absolute, log


In [39]:

# Update the scatter plot with the sorted dataframe
fig = px.strip(sorted_df_absolute, x='adjusted_clinical_error_absolute_log', y='calculator_arm', title='Adjusted Clinical Error Absolute by Calculator-Arm Permutations')
fig.update_traces(jitter=0.2)

# Update layout for better visualization
fig.update_traces(marker=dict(opacity=0.2))  # Set marker opacity to 0.05 for semi-transparency
fig.update_layout(
    xaxis_title='Numeric error, absolute, normalized to calculator range',
    yaxis_title='Calculator-Arm Permutations',
    width=1000,
    height=1200,
    font=dict(
        family="Arial",
        size=8,
        color="Black"
    ),
    plot_bgcolor="white",
    margin_t=50,
    margin_b=50,
    margin_l=50,
    margin_r=50,
    xaxis=dict(range=[0, 4]),  # Set x-axis range for absolute values
    annotations=[
        dict(
            x=100,
            y='cci - llama_ci',
            xref='x',
            yref='y',
            text='Not shown: One data point > 100',
            showarrow=True,
            arrowhead=2,
            ax=-100,
            ay=-0
        ),
        dict(
            text=exclusion_note,
            align='left',
            # showarrow=False,
            xref='x',
            yref='y',
            x=0,
            y="Multiple*",
            bordercolor='black',
            borderwidth=1,
            ax=150,
            ay=30
        )
    ]
)

util.save_fig(fig, "adjusted_clinical_error_absolute_by_calculator_arm")
fig.show()

Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/adjusted_clinical_error_absolute_by_calculator_arm.svg
Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/adjusted_clinical_error_absolute_by_calculator_arm.png


# Single color box charts

### By Calculator

In [40]:
fig = px.box(sorted_df_absolute, x="adjusted_clinical_error_absolute_log", y="calculator_slug", points="all",  height=1500, width=1000)
fig.update_traces(jitter=0.5)

# # Update the scatter plot with the sorted dataframe
# fig_absolute = px.scatter(, x='', y='', title='')

# Update layout for better visualization
fig.update_traces(marker=dict(opacity=0.2))  # Set marker opacity to 0.05 for semi-transparency
fig.update_layout(
    xaxis_title='Numeric error, absolute, normalized to calculator range (log10)',
    yaxis_title='Calculator',
    width=1000,
    height=800,
    font=dict(
        family="Arial",
        size=12,
        color="Black"
    ),
    plot_bgcolor="white",
    margin_t=50,
    margin_b=50,
    margin_l=50,
    margin_r=50,
)
util.save_fig(fig, "box_plot_adjusted_clinical_error_absolute_by_calculator")
fig.show()

Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/box_plot_adjusted_clinical_error_absolute_by_calculator.svg
Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/box_plot_adjusted_clinical_error_absolute_by_calculator.png


### By arm

In [368]:
fig = px.box(sorted_df_absolute, x="adjusted_clinical_error_absolute_log", y="arm_name", points="all", height=1500, width=1000)
fig.update_traces(jitter=0.1)

# Update layout for better visualization
fig.update_traces(marker=dict(opacity=0.1))  # Set marker opacity to 0.2 for semi-transparency
fig.update_layout(
    xaxis_title='Numeric error, absolute, normalized to calculator range (log10)',
    yaxis_title='Arm',
    width=1000,
    height=800,
    font=dict(
        family="Arial",
        size=12,
        color="Black"
    ),
    plot_bgcolor="white",
    yaxis_showline=True,
    yaxis_gridwidth=11,
    yaxis_linewidth=11,
    title_font_size=24,
    margin_t=0,
    margin_b=0,
    margin_l=0,
    margin_r=0,
    xaxis=dict(
        type='linear',  # Set x-axis to logarithmic scale
        # range=[-6, 8]  # Set x-axis range for absolute values
    )
)



util.save_fig(fig, "box_plot_adjusted_clinical_error_absolute_by_arm", upload=True)
fig.show()



Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/box_plot_adjusted_clinical_error_absolute_by_arm.svg
Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/box_plot_adjusted_clinical_error_absolute_by_arm.png
View this figure on Plotly: https://plotly.com/~alexgoodell/71/)


# Violin charts of errors by specific calc-arm combinations

In [370]:
from pyparsing import line

for calc_slug in df.calculator_slug.unique():
    fig = px.violin(sorted_df_absolute[sorted_df_absolute.calculator_slug == calc_slug], x="adjusted_clinical_error_absolute_log", y="arm_name",  color="arm_name")
    fig.update_traces(
        pointpos=-0.25,
        points='all',
        jitter=0,
        marker=dict(
            opacity=0.2,
            symbol='square',
            size=15,
        ),
        line=dict(
            width=1
        ),
        side='positive',
        # spanmode='hard',
        meanline=dict(
            visible=True,
            width=2,
        )
    )
    fig.update_layout(
        title=f"Severity of error in calculation {calc_slug} tasks by arm",
        xaxis_title='Numeric error, absolute, normalized to calculator range (log10)',
        yaxis_title='Arm',
        width=1000,
        height=600,
        font=dict(
            family="Arial",
            size=12,
            color="Black"
        ),
        plot_bgcolor="white",
        # xaxis=dict(
        #     type='linear',  # Set x-axis to logarithmic scale
        #     range=[-8, 8]  # Set x-axis range for absolute values
        # ),
        # yaxis=dict(
        #     type='category',
        #     categoryorder='array',
        #     categoryarray=sorted_df_absolute.arm_slug.unique()
        # ),
        violinmode='overlay',
        violingap=0,
        violingroupgap=0,
    )
    util.save_fig(fig, f"{calc_slug}_violin_plot_adjusted_clinical_error_absolute_by_arm", upload=False)





Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/nihss_violin_plot_adjusted_clinical_error_absolute_by_arm.svg
Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/nihss_violin_plot_adjusted_clinical_error_absolute_by_arm.png
Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/psiport_violin_plot_adjusted_clinical_error_absolute_by_arm.svg
Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/psiport_violin_plot_adjusted_clinical_error_absolute_by_arm.png
Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/hasbled_violin_plot_adjusted_clinical_error_absolute_by_arm.svg
Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/hasbled_violin_plot_adjusted_clinical_error_absolute_by_arm.png
Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/meldna_violin_plot_adjusted_clinical_error_absolute_by_arm.svg
Figure saved to /Users/alexandergoodell/code/l

# Error as a percent of reference answer

In [ ]:

ordering = {
    "performance":['Correct', 'Incorrect', 'No valid output'],
    'arm_name': [
          'Llama Base',
          'Llama + CI',
          'Llama + RAG',
          'Llama + RAG + CI',
          'Llama + OMC',
          'GPT4 Base',
          'GPT4 + CI',
          'GPT4 + RAG',
          'GPT4 + RAG + CI',
          'GPT4 + OMC'],
    #[a.name for a in datacore.arms],
    'models': [m.name for m in datacore.models], # type: ignore
    
}

# Sort the dataframe by arm_name as listed in the ordering dictionary but reversed in order to have the correct order in the plot
arm_order = ordering['arm_name']
arm_order.reverse()
sorted_df_absolute = sorted_df_absolute.set_index('arm_name').loc[arm_order].reset_index()


# Define the color map based on the ordering variable
color_map = {name: color for name, color in zip(ordering['arm_name'], px.colors.qualitative.G10)}


In [415]:
caption = "Box plot of numeric error as a percent of reference answer"
xtitle = "Numeric error as a percent of reference answer(log10)"

fig = px.box(sorted_df_absolute, 
             x="percentage_error_absolute_log", 
             y="calculator_name", 
             points="all", 
             color="arm_name", 
             hover_data=["output_answer", 
                         "reference_answer", 
                         "mild_cutoff", 
                         "severe_cutoff",
                         "minimum_score",
                         "maximum_score",
                         "adjusted_clinical_error_absolute", 
                         "adjusted_clinical_error_2_absolute"],
            color_discrete_map=color_map,
            )

# Update layout for better visualization
fig.update_traces(
    marker=dict(
        opacity=0.05,
        symbol='square',
        size=8,
    ),
    pointpos=-0,
    boxpoints='all',
    jitter=0.5,
    line=dict(
        width=0.5,
    ),
    whiskerwidth=0.2,
    boxmean=True,
)

fig.update_layout(
    margin=dict(t=0, b=0, l=0, r=20, pad=10),
    xaxis_title=xtitle,
    yaxis_title='Arm',
    font=dict(
        family="Arial",
        size=12,
        color="Black"
    ),
    plot_bgcolor="white",
    width=1000,
    height=800,
    xaxis=dict(
        type='linear',
        range=[-0.01, 3.01],
        gridcolor='rgba(0,0,0,0.15)',
        gridwidth=1,
        zeroline=True,
        zerolinewidth=1,
        zerolinecolor='rgba(0,0,0,0.15)',
        showgrid=True,
        tickvals=[0, 1, 2, 3],
        ticktext=["1%", "10%", "100%", "1000%"]
    ),
    yaxis=dict(
        type='category',
        categoryorder='array',
        categoryarray=sorted_df_absolute.arm_name.unique(),
        gridcolor='rgba(0,0,0,0.15)',
        gridwidth=4,
        zeroline=True,
        zerolinewidth=1,
        zerolinecolor='rgba(0,0,0,0.15)',
        showgrid=True,
        tickson='boundaries'
    ),
    boxgroupgap=0.65,
    boxgap=0.15,
    boxmode='group',
    legend=dict(
        orientation="v",
        yanchor="bottom",
        y=0.02,
        xanchor="right",
        x=0.98,
    ),
)
 
filename = util.slugify(caption)
util.save_fig(fig, filename, upload=False)
fig.show()

Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/boxplotofnumericerrorasapercentofreferenceanswer.svg
Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/boxplotofnumericerrorasapercentofreferenceanswer.png


In [ ]:
caption = "Box plot of numeric error as a percent of calculator's normal reference range by arm and calculator"
xtitle = "Numeric error as a percent of calculator's normal reference range (log10)"

fig = px.box(sorted_df_absolute, 
             x="adjusted_clinical_error_absolute_log", 
             y="calculator_name", 
             points="all", 
             color="arm_name", 
             hover_data=["output_answer", 
                         "reference_answer", 
                         "mild_cutoff", 
                         "severe_cutoff",
                         "minimum_score",
                         "maximum_score",
                         "adjusted_clinical_error_absolute", 
                         "adjusted_clinical_error_2_absolute"],
            color_discrete_map=color_map,
            )

# Update layout for better visualization
fig.update_traces(
    marker=dict(
        opacity=0.05,
        symbol='square',
        size=8,
    ),
    pointpos=-0,
    boxpoints='all',
    jitter=0.5,
    line=dict(
        width=0.5,
    ),
    whiskerwidth=0.2,
    boxmean=True,
)

fig.update_layout(
    margin=dict(t=0, b=0, l=0, r=20, pad=10),
    xaxis_title=xtitle,
    yaxis_title='Arm',
    font=dict(
        family="Arial",
        size=12,
        color="Black"
    ),
    plot_bgcolor="white",
    width=1000,
    height=800,
    xaxis=dict(
        type='linear',
        range=[-0.01, 3.01],
        gridcolor='rgba(0,0,0,0.15)',
        gridwidth=1,
        zeroline=True,
        zerolinewidth=1,
        zerolinecolor='rgba(0,0,0,0.15)',
        showgrid=True,
        tickvals=[0, 1, 2, 3],
        ticktext=["1%", "10%", "100%", "1000%"]
    ),
    yaxis=dict(
        type='category',
        categoryorder='array',
        categoryarray=sorted_df_absolute.arm_name.unique(),
        gridcolor='rgba(0,0,0,0.15)',
        gridwidth=4,
        zeroline=True,
        zerolinewidth=1,
        zerolinecolor='rgba(0,0,0,0.15)',
        showgrid=True,
        tickson='boundaries'
    ),
    boxgroupgap=0.65,
    boxgap=0.15,
    boxmode='group',
    legend=dict(
        orientation="v",
        yanchor="bottom",
        y=0.02,
        xanchor="right",
        x=0.98,
    ),
)

filename = util.slugify(caption)
util.save_fig(fig, filename, upload=False)
# fig.show()


Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/boxplotofnumericerrorasapercentofcalculatorsnormalreferencerangebyarmandcalculator.svg
Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/boxplotofnumericerrorasapercentofcalculatorsnormalreferencerangebyarmandcalculator.png


In [412]:
caption = "Box plot of numeric error as a percent of calculator's minimum and maximum values by arm and calculator"
xtitle = "Numeric error as a percent of calculator's minimum and maximum values (log10)"

fig = px.box(sorted_df_absolute, 
             x="adjusted_clinical_error_2_absolute_log", 
             y="calculator_name", 
             points="all", 
             color="arm_name", 
             hover_data=["output_answer", 
                         "reference_answer", 
                         "mild_cutoff", 
                         "severe_cutoff",
                         "minimum_score",
                         "maximum_score",
                         "adjusted_clinical_error_absolute", 
                         "adjusted_clinical_error_2_absolute"],
            color_discrete_map=color_map,
            )

# Update layout for better visualization
fig.update_traces(
    marker=dict(
        opacity=0.05,
        symbol='square',
        size=8,
    ),
    pointpos=-0,
    boxpoints='all',
    jitter=0.5,
    line=dict(
        width=0.5,
    ),
    whiskerwidth=0.2,
    boxmean=True,
)

fig.update_layout(
    margin=dict(t=0, b=0, l=0, r=20, pad=10),
    xaxis_title=xtitle,
    yaxis_title='Arm',
    font=dict(
        family="Arial",
        size=12,
        color="Black"
    ),
    plot_bgcolor="white",
    width=1000,
    height=800,
    xaxis=dict(
        type='linear',
        range=[-0.01, 3.01],
        gridcolor='rgba(0,0,0,0.15)',
        gridwidth=1,
        zeroline=True,
        zerolinewidth=1,
        zerolinecolor='rgba(0,0,0,0.15)',
        showgrid=True,
        tickvals=[0, 1, 2, 3],
        ticktext=["1%", "10%", "100%", "1000%"]
    ),
    yaxis=dict(
        type='category',
        categoryorder='array',
        categoryarray=sorted_df_absolute.arm_name.unique(),
        gridcolor='rgba(0,0,0,0.15)',
        gridwidth=4,
        zeroline=True,
        zerolinewidth=1,
        zerolinecolor='rgba(0,0,0,0.15)',
        showgrid=True,
        tickson='boundaries'
    ),
    boxgroupgap=0.65,
    boxgap=0.15,
    boxmode='group',
    legend=dict(
        orientation="v",
        yanchor="bottom",
        y=0.02,
        xanchor="right",
        x=0.98,
    ),
)

filename = util.slugify(caption)
util.save_fig(fig, filename, upload=False)
# fig.show()

Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/boxplotofnumericerrorasapercentofcalculatorsminimumandmaximumvaluesbyarmandcalculator.svg
Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/boxplotofnumericerrorasapercentofcalculatorsminimumandmaximumvaluesbyarmandcalculator.png


# Swap the index to show arm->calculator

In [416]:
caption = "Box plot of numeric error as a percent of reference answer by arm then calculator"
xtitle = "Numeric error as a percent of reference answer(log10)"

fig = px.box(sorted_df_absolute, 
             x="percentage_error_absolute_log", 
             y="arm_name", 
             points="all", 
             color="calculator_name", 
             hover_data=["output_answer", 
                         "reference_answer", 
                         "mild_cutoff", 
                         "severe_cutoff",
                         "minimum_score",
                         "maximum_score",
                         "adjusted_clinical_error_absolute", 
                         "adjusted_clinical_error_2_absolute"],
            color_discrete_map=color_map,
            )

# Update layout for better visualization
fig.update_traces(
    marker=dict(
        opacity=0.05,
        symbol='square',
        size=8,
    ),
    pointpos=-0,
    boxpoints='all',
    jitter=0.5,
    line=dict(
        width=0.5,
    ),
    whiskerwidth=0.2,
    boxmean=True,
)

fig.update_layout(
    margin=dict(t=0, b=0, l=0, r=20, pad=10),
    xaxis_title=xtitle,
    yaxis_title='Arm',
    font=dict(
        family="Arial",
        size=12,
        color="Black"
    ),
    plot_bgcolor="white",
    width=1000,
    height=800,
    xaxis=dict(
        type='linear',
        range=[-0.01, 3.01],
        gridcolor='rgba(0,0,0,0.15)',
        gridwidth=1,
        zeroline=True,
        zerolinewidth=1,
        zerolinecolor='rgba(0,0,0,0.15)',
        showgrid=True,
        tickvals=[0, 1, 2, 3],
        ticktext=["1%", "10%", "100%", "1000%"]
    ),
    yaxis=dict(
        type='category',
        categoryorder='array',
        categoryarray=sorted_df_absolute.arm_name.unique(),
        gridcolor='rgba(0,0,0,0.15)',
        gridwidth=4,
        zeroline=True,
        zerolinewidth=1,
        zerolinecolor='rgba(0,0,0,0.15)',
        showgrid=True,
        tickson='boundaries'
    ),
    boxgroupgap=0.65,
    boxgap=0.15,
    boxmode='group',
    legend=dict(
        orientation="v",
        yanchor="bottom",
        y=0.02,
        xanchor="right",
        x=0.98,
    ),
)
 
filename = util.slugify(caption)
util.save_fig(fig, filename, upload=False)
fig.show()

Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/boxplotofnumericerrorasapercentofreferenceanswerbyarmthencalculator.svg
Figure saved to /Users/alexandergoodell/code/llm-calc/manuscript/figures/boxplotofnumericerrorasapercentofreferenceanswerbyarmthencalculator.png
